## Check GPU

In [1]:
from distutils.version import LooseVersion
import warnings
import tensorflow as tf

# Check TensorFlow Version
assert LooseVersion(tf.__version__) >= LooseVersion('1.0'), 'Please use TensorFlow version 1.0 or newer.  You are using {}'.format(tf.__version__)
print('TensorFlow Version: {}'.format(tf.__version__))

# Check for a GPU
if not tf.test.gpu_device_name():
    warnings.warn('No GPU found. Please ensure you have installed TensorFlow correctly')
else:
    print('Default GPU Device: {}'.format(tf.test.gpu_device_name()))
    
print("Num GPUs Available: ", len(tf.config.list_physical_devices('GPU')))

TensorFlow Version: 2.6.0
Default GPU Device: /device:GPU:0
Num GPUs Available:  1


In [2]:
from tensorflow.python.client import device_lib
device_lib.list_local_devices()

[name: "/device:CPU:0"
 device_type: "CPU"
 memory_limit: 268435456
 locality {
 }
 incarnation: 17875864096839324546,
 name: "/device:GPU:0"
 device_type: "GPU"
 memory_limit: 9898950656
 locality {
   bus_id: 1
   links {
   }
 }
 incarnation: 8683298867691047183
 physical_device_desc: "device: 0, name: NVIDIA GeForce RTX 3080 Ti, pci bus id: 0000:01:00.0, compute capability: 8.6"]

## Import Libraries

In [3]:
import numpy as np
import pandas as pd

import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, InputLayer, Dropout
from tensorflow.keras.losses import mean_absolute_error, mean_squared_error
from tensorflow.keras.optimizers import Nadam, Adam
from tensorflow.keras.initializers import lecun_normal

import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots

#### California Housing Dataset
https://www.dcc.fc.up.pt/~ltorgo/Regression/cal_housing.html 

In [4]:
df_train = pd.read_csv("california_housing_train.csv")
df_test = pd.read_csv("california_housing_test.csv")

#### The dataset is splitted into 8.5:1.5 (Train:Test) ratio.

In [44]:
print(len(df_train))
print(len(df_test))

17000
3000


In [5]:
df_train.head()

longitude  latitude  housing_median_age  total_rooms  total_bedrooms  \
0    -114.31     34.19                15.0       5612.0          1283.0   
1    -114.47     34.40                19.0       7650.0          1901.0   
2    -114.56     33.69                17.0        720.0           174.0   
3    -114.57     33.64                14.0       1501.0           337.0   
4    -114.57     33.57                20.0       1454.0           326.0   

   population  households  median_income  median_house_value  
0      1015.0       472.0         1.4936             66900.0  
1      1129.0       463.0         1.8200             80100.0  
2       333.0       117.0         1.6509             85700.0  
3       515.0       226.0         3.1917             73400.0  
4       624.0       262.0         1.9250             65500.0

### Drop features accordingly and choose the target feature

In [6]:
df_train = df_train.drop(["longitude", "latitude", "housing_median_age","households","median_income","total_rooms", "total_bedrooms"], axis=1)
df_test = df_test.drop(["longitude", "latitude", "housing_median_age","households","median_income","total_rooms", "total_bedrooms"], axis=1)

In [7]:
from sklearn.preprocessing import StandardScaler

X_train = df_train.drop([ "median_house_value",], axis=1).values
y_train = df_train.median_house_value.values
X_test = df_test.drop(["median_house_value",], axis=1).values
y_test = df_test.median_house_value.values

In [8]:
scaler = StandardScaler()

X_train_norm = scaler.fit_transform(X_train)
X_test_norm = scaler.transform(X_test)

### Using Callbacks to avoid using too many unnecessary epochs
Change the value of 'patience' accordingly, for the model to check if the evaluation metrics is not improving   

In [9]:
callback = tf.keras.callbacks.EarlyStopping(monitor='val_loss', patience=10)

## Not Using Monte Carlo Dropout

### Lightweight Model (Regular)

In [10]:
model_NN_light = Sequential([InputLayer(input_shape=(1,)),
             Dropout(0.4),          
             Dense(100, activation="relu", kernel_initializer="lecun_normal"),
             Dropout(0.4),
             Dense(200, activation="relu", kernel_initializer="lecun_normal"),
             Dropout(0.4),
             Dense(200, activation="relu", kernel_initializer="lecun_normal"),
             Dropout(0.4),
             Dense(100, activation="relu", kernel_initializer="lecun_normal"),
             Dropout(0.4),
             Dense(1, activation=None)
             ])
print(model_NN_light)

In [11]:
model_NN_light.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dropout (Dropout)            (None, 1)                 0         
_________________________________________________________________
dense (Dense)                (None, 100)               200       
_________________________________________________________________
dropout_1 (Dropout)          (None, 100)               0         
_________________________________________________________________
dense_1 (Dense)              (None, 200)               20200     
_________________________________________________________________
dropout_2 (Dropout)          (None, 200)               0         
_________________________________________________________________
dense_2 (Dense)              (None, 200)               40200     
_________________________________________________________________
dropout_3 (Dropout)          (None, 200)               0

In [12]:
model_NN_light.compile(loss="mean_squared_error",
              optimizer="Nadam",
              metrics=["mean_squared_error"])

In [13]:
history_NN_light = model_NN_light.fit(X_train_norm, y_train, epochs=201, validation_split=0.2, callbacks=[callback])

Epoch 1/201
425/425 [==============================] - 4s 7ms/step - loss: 29605449728.0000 - mean_squared_error: 29605449728.0000 - val_loss: 24009990144.0000 - val_mean_squared_error: 24009990144.0000
Epoch 2/201
425/425 [==============================] - 4s 9ms/step - loss: 15972195328.0000 - mean_squared_error: 15972195328.0000 - val_loss: 20263018496.0000 - val_mean_squared_error: 20263018496.0000
Epoch 3/201
425/425 [==============================] - 4s 10ms/step - loss: 14420820992.0000 - mean_squared_error: 14420820992.0000 - val_loss: 19543795712.0000 - val_mean_squared_error: 19543795712.0000
Epoch 4/201
425/425 [==============================] - 4s 9ms/step - loss: 13749939200.0000 - mean_squared_error: 13749939200.0000 - val_loss: 20615002112.0000 - val_mean_squared_error: 20615002112.0000
Epoch 5/201
425/425 [==============================] - 4s 10ms/step - loss: 13731866624.0000 - mean_squared_error: 13731866624.0000 - val_loss: 20337242112.0000 - val_mean_squared_error: 

In [14]:
# weight adjustment due to dropout
WEIGHTS = model_NN_light.get_weights()
WEIGHTS[0] *= 1/0.4
model_NN_light.set_weights(WEIGHTS)

In [15]:
df_train.head(2)

population  median_house_value
0      1015.0             66900.0
1      1129.0             80100.0

In [16]:
predictions = model_NN_light.predict(X_test_norm)

In [17]:
df_test["predictions"] = predictions

In [18]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=df_test.population, y=df_test.median_house_value, mode="markers"))
fig.add_trace(go.Scatter(x=df_test.population, y=df_test.predictions, mode="markers"))

fig.show()

### Heavyweight Model (Regular)

In [19]:
model_NN_heavy = Sequential([InputLayer(input_shape=(1,)),
             Dropout(0.4),          
             Dense(1000, activation="relu", kernel_initializer="lecun_normal"),
             Dropout(0.4),
             Dense(1000, activation="relu", kernel_initializer="lecun_normal"),
             Dropout(0.4),
             Dense(2000, activation="relu", kernel_initializer="lecun_normal"),
             Dropout(0.4),
             Dense(2000, activation="relu", kernel_initializer="lecun_normal"),
             Dropout(0.4),
             Dense(1000, activation="relu", kernel_initializer="lecun_normal"),
             Dropout(0.4),
             Dense(1, activation=None)
             ])
print(model_NN_heavy)

In [20]:
model_NN_heavy.summary()

Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dropout_5 (Dropout)          (None, 1)                 0         
_________________________________________________________________
dense_5 (Dense)              (None, 1000)              2000      
_________________________________________________________________
dropout_6 (Dropout)          (None, 1000)              0         
_________________________________________________________________
dense_6 (Dense)              (None, 1000)              1001000   
_________________________________________________________________
dropout_7 (Dropout)          (None, 1000)              0         
_________________________________________________________________
dense_7 (Dense)              (None, 2000)              2002000   
_________________________________________________________________
dropout_8 (Dropout)          (None, 2000)             

In [21]:
model_NN_heavy.compile(loss="mean_squared_error",
              optimizer="Nadam",
              metrics=["mean_squared_error"])

In [22]:
history_NN_heavy = model_NN_heavy.fit(X_train_norm, y_train, epochs=201, validation_split=0.2, callbacks=[callback])

Epoch 1/201
425/425 [==============================] - 5s 10ms/step - loss: 17656913920.0000 - mean_squared_error: 17656913920.0000 - val_loss: 19352459264.0000 - val_mean_squared_error: 19352459264.0000
Epoch 2/201
425/425 [==============================] - 4s 10ms/step - loss: 13510360064.0000 - mean_squared_error: 13510360064.0000 - val_loss: 16837670912.0000 - val_mean_squared_error: 16837670912.0000
Epoch 3/201
425/425 [==============================] - 4s 10ms/step - loss: 13283505152.0000 - mean_squared_error: 13283505152.0000 - val_loss: 18379104256.0000 - val_mean_squared_error: 18379104256.0000
Epoch 4/201
425/425 [==============================] - 4s 10ms/step - loss: 13286567936.0000 - mean_squared_error: 13286567936.0000 - val_loss: 19538284544.0000 - val_mean_squared_error: 19538284544.0000
Epoch 5/201
425/425 [==============================] - 4s 10ms/step - loss: 13315142656.0000 - mean_squared_error: 13315142656.0000 - val_loss: 18128340992.0000 - val_mean_squared_erro

In [23]:
# weight adjustment due to dropout
WEIGHTS = model_NN_heavy.get_weights()
WEIGHTS[0] *= 1/0.4
model_NN_heavy.set_weights(WEIGHTS)

In [24]:
df_train.head(2)

population  median_house_value
0      1015.0             66900.0
1      1129.0             80100.0

In [25]:
predictions = model_NN_heavy.predict(X_test_norm)

In [26]:
df_test["predictions"] = predictions

In [27]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=df_test.population, y=df_test.median_house_value, mode="markers"))
fig.add_trace(go.Scatter(x=df_test.population, y=df_test.predictions, mode="markers"))

fig.show()

## Using Monte Carlo Dropout

We simply overwrite the method to turn the dropout technique on in the testing phase as well

In [28]:
class MCDropout(Dropout):
    def call(self, inputs):
        return super().call(inputs, training=True)
    

### Lightweight Model (MC)

In [29]:
model_MC_light = Sequential([InputLayer(input_shape=(1,)),
             MCDropout(0.4),          
             Dense(100, activation="relu", kernel_initializer="lecun_normal"),
             MCDropout(0.4),
             Dense(200, activation="relu", kernel_initializer="lecun_normal"),
             MCDropout(0.4),
             Dense(200, activation="relu", kernel_initializer="lecun_normal"),
             MCDropout(0.4),
             Dense(100, activation="relu", kernel_initializer="lecun_normal"),
             MCDropout(0.4),
             Dense(1, activation=None)
             ])

In [30]:
model_MC_light.summary()


Model: "sequential_2"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
mc_dropout (MCDropout)       (None, 1)                 0         
_________________________________________________________________
dense_11 (Dense)             (None, 100)               200       
_________________________________________________________________
mc_dropout_1 (MCDropout)     (None, 100)               0         
_________________________________________________________________
dense_12 (Dense)             (None, 200)               20200     
_________________________________________________________________
mc_dropout_2 (MCDropout)     (None, 200)               0         
_________________________________________________________________
dense_13 (Dense)             (None, 200)               40200     
_________________________________________________________________
mc_dropout_3 (MCDropout)     (None, 200)              

In [31]:
model_MC_light.compile(loss="mean_squared_error",
              optimizer="Nadam",
              metrics=["mean_squared_error"])

In [32]:
history_MC_light = model_MC_light.fit(X_train_norm, y_train, epochs=200, validation_split=0.2, callbacks=[callback])

Epoch 1/200
425/425 [==============================] - 4s 8ms/step - loss: 27748853760.0000 - mean_squared_error: 27748853760.0000 - val_loss: 25316454400.0000 - val_mean_squared_error: 25316454400.0000
Epoch 2/200
425/425 [==============================] - 4s 9ms/step - loss: 14788104192.0000 - mean_squared_error: 14788104192.0000 - val_loss: 21069961216.0000 - val_mean_squared_error: 21069961216.0000
Epoch 3/200
425/425 [==============================] - 4s 9ms/step - loss: 13878960128.0000 - mean_squared_error: 13878960128.0000 - val_loss: 20582518784.0000 - val_mean_squared_error: 20582518784.0000
Epoch 4/200
425/425 [==============================] - 3s 8ms/step - loss: 13518361600.0000 - mean_squared_error: 13518361600.0000 - val_loss: 20375926784.0000 - val_mean_squared_error: 20375926784.0000
Epoch 5/200
425/425 [==============================] - 4s 9ms/step - loss: 13569750016.0000 - mean_squared_error: 13569750016.0000 - val_loss: 21484328960.0000 - val_mean_squared_error: 21

In [33]:
# weight adjustment due to dropout
WEIGHTS = model_MC_light.get_weights()
WEIGHTS[0] *= 1/0.4
model_MC_light.set_weights(WEIGHTS)

In [34]:
y_pred_stack = np.stack([model_MC_light.predict(X_test_norm) for sample in range(10)])

In [35]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=df_test.population, y=df_test.median_house_value, mode="markers"))
for i in range(len(y_pred_stack)):

    fig.add_trace(go.Scatter(x=df_test.population, y=y_pred_stack[i].reshape(-1,), mode="markers", opacity=0.1,  marker=dict(
            color='Red')))

fig.show()

The plot is quite spread and wide

### Heaveweight Model (MC)

In [36]:
model_MC_heavy = Sequential([InputLayer(input_shape=(1,)),
             MCDropout(0.4),          
             Dense(1000, activation="relu", kernel_initializer="lecun_normal"),
             MCDropout(0.4),
             Dense(1000, activation="relu", kernel_initializer="lecun_normal"),
             MCDropout(0.4),
             Dense(2000, activation="relu", kernel_initializer="lecun_normal"),
             MCDropout(0.4),
             Dense(2000, activation="relu", kernel_initializer="lecun_normal"),
             MCDropout(0.4),
             Dense(1000, activation="relu", kernel_initializer="lecun_normal"),
             MCDropout(0.4),
             Dense(1, activation=None)
             ])

In [37]:
model_MC_heavy.summary()


Model: "sequential_3"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
mc_dropout_5 (MCDropout)     (None, 1)                 0         
_________________________________________________________________
dense_16 (Dense)             (None, 1000)              2000      
_________________________________________________________________
mc_dropout_6 (MCDropout)     (None, 1000)              0         
_________________________________________________________________
dense_17 (Dense)             (None, 1000)              1001000   
_________________________________________________________________
mc_dropout_7 (MCDropout)     (None, 1000)              0         
_________________________________________________________________
dense_18 (Dense)             (None, 2000)              2002000   
_________________________________________________________________
mc_dropout_8 (MCDropout)     (None, 2000)             

In [38]:
model_MC_heavy.compile(loss="mean_squared_error",
              optimizer="Nadam",
              metrics=["mean_squared_error"])

In [39]:
history_MC_heavy = model_MC_heavy.fit(X_train_norm, y_train, epochs=200, validation_split=0.2, callbacks=[callback])

Epoch 1/200
425/425 [==============================] - 5s 11ms/step - loss: 17611278336.0000 - mean_squared_error: 17611278336.0000 - val_loss: 17869496320.0000 - val_mean_squared_error: 17869496320.0000
Epoch 2/200
425/425 [==============================] - 4s 10ms/step - loss: 13449282560.0000 - mean_squared_error: 13449282560.0000 - val_loss: 19761350656.0000 - val_mean_squared_error: 19761350656.0000
Epoch 3/200
425/425 [==============================] - 4s 10ms/step - loss: 13282202624.0000 - mean_squared_error: 13282202624.0000 - val_loss: 21133776896.0000 - val_mean_squared_error: 21133776896.0000
Epoch 4/200
425/425 [==============================] - 4s 10ms/step - loss: 13318580224.0000 - mean_squared_error: 13318580224.0000 - val_loss: 20077113344.0000 - val_mean_squared_error: 20077113344.0000
Epoch 5/200
425/425 [==============================] - 4s 10ms/step - loss: 13161405440.0000 - mean_squared_error: 13161405440.0000 - val_loss: 19969955840.0000 - val_mean_squared_erro

In [40]:
# weight adjustment due to dropout
WEIGHTS = model_MC_heavy.get_weights()
WEIGHTS[0] *= 1/0.4
model_MC_heavy.set_weights(WEIGHTS)

In [41]:
y_pred_stack = np.stack([model_MC_heavy.predict(X_test_norm) for sample in range(10)])

In [42]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=df_test.population, y=df_test.median_house_value, mode="markers"))
for i in range(len(y_pred_stack)):

    fig.add_trace(go.Scatter(x=df_test.population, y=y_pred_stack[i].reshape(-1,), mode="markers", opacity=0.1,  marker=dict(
            color='Red')))

fig.show()

The plot for the heavyweight model is more packed than the previous one, which shows that the model is less uncertain and more confident than the previous model